# This notebook compares output from the original TIEGCM reader to the edited one
#### We attempt to validate the accuracy by comparing to other sources of density measurements.

- We sample the TIEGCM model along the orbit of Aqua.  Ephemeris data comes from:https://sscweb.gsfc.nasa.gov/cgi-bin/Locator.cgi 
- We compare outputs from the original tiegcm.py code to the new edited one to include improved extrapolation above the boundary and conversion of constituends from MMR.
    - helium is included in the above boundary extrap
    - extraps from the 25th pressure level to avoid numerical issues
    - change any use of 'Z' for the vertical coordinate to "ZG"
    - ~~any points that exist on the midpoint levels use ZGMID as vertical~~. (not implemented yet)


In [1]:
%load_ext autoreload
%autoreload 2

import warnings
warnings.filterwarnings(action='ignore')

import pandas as pd
import numpy as np
from scipy.spatial import kdtree
from scipy.interpolate import griddata, LinearNDInterpolator
import scipy
from netCDF4 import Dataset
from plotly.offline import plot, iplot
import plotly.graph_objs as go
from plotly.graph_objs import Layout
import plotly
import matplotlib.pyplot as plt
# import antlr4 

plotly.offline.init_notebook_mode(connected=True)

In [2]:
# import TIEGCM object with the following convention
from tiegcm.tiegcm import TIEGCM, Point3D, Point4D, Slice_key4D, ColumnSlice4D, ColumnSlice3D, Model_Manager
from tiegcm.util import average_longitude
from tiegcm.util import *

In [3]:
# import TIEGCM object with the following convention
from tiegcm_orig.tiegcm_orig import TIEGCM as TIEGCM_orig
from tiegcm_orig.tiegcm_orig import Point3D as Point3D_orig
from tiegcm_orig.tiegcm_orig import Point4D as Point4D_orig
from tiegcm_orig.tiegcm_orig import Slice_key4D as Slice_key4D_orig
from tiegcm_orig.tiegcm_orig import ColumnSlice4D as ColumnSlice4D_orig
from tiegcm_orig.tiegcm_orig import ColumnSlice3D as ColumnSlice3D_orig
from tiegcm_orig.tiegcm_orig import Model_Manager as Model_Manager_orig
from tiegcm_orig.util import *

#### First Import Aqua Orbit data and save to a pandas dataframe

In [4]:
# times = ['2013_03_01_to_2013_03_04', '2013_03_13_to_2013_03_23']

def import_ephemeris(time_string):
    aqua_orbit_file = "../../Summer2019_data/aqua_orbit/aqua_data_" + time_string + ".csv"

    # import data
    aqua_data_raw = pd.read_csv(aqua_orbit_file, 
                             skiprows = 4 ,
                             names = ['date', 'X_geo','Y_geo','Z_geo','lat','lon','local_time_geo','radius'],
                             parse_dates = True,
                              )
    # convert to dataframe
    aqua_ephemeris = pd.DataFrame(aqua_data_raw)

    # change the date column to be datetime object
    aqua_ephemeris['date'] = pd.to_datetime(aqua_ephemeris['date'],format = ('%y/%m/%d %H:%M:%f'))  

    # reformat the datetime object string so that tiegcm.py's Model_Manager can read it ('%y-%m-%d %H:%M:%S')
#     date_formatted = aqua_ephemeris['date'].dt.strftime('%y-%m-%d %H:%M:%S')


    #-------------------
    # add altitude

    R_e = 6378.137   # km 
    altitude_aqua = aqua_ephemeris.radius - R_e
    aqua_ephemeris['altitude'] = altitude_aqua 
    return aqua_ephemeris

#### Make a callable function that samples the TIEGCM along the orbit of a satelite using the different readers

In [5]:
def sample_TIEGCM(files, tiegcm_version, time_string,ID):
    if tiegcm_version == "original":
        tiegcm = Model_Manager_orig(files)
    elif tiegcm_version == "edited":
        tiegcm = Model_Manager(files)
    density_model = []
    title_y_string =  'density from ' + tiegcm_version + ' reader, ' + ID
    title_string = tiegcm_version +' TIEGCM sampled using Aqua'

    aqua_ephemeris = import_ephemeris(time_string)
    date_formatted = aqua_ephemeris['date'].dt.strftime('%y-%m-%d %H:%M:%S')
    
    counter = 0
    
    for i,idate in enumerate(aqua_ephemeris['date']):
        xlon = np.round(np.array(aqua_ephemeris['lon'][i]) , decimals=2)
        xlat = np.round(np.array(aqua_ephemeris['lat'][i])  , decimals=2)
        xalt = np.round(aqua_ephemeris['altitude'][i] , decimals=2) *1e5
        idate = aqua_ephemeris['date'][i]
        time = date_formatted[i]
        if (counter == 5):
            print 'time = ', time
            counter = 0
#         print 'time = ', time
        density_model.append(tiegcm.density(xlat, xlon, xalt,  idate ))
        
        counter += 1
        
    plot_dens = go.Scatter(
                    x = aqua_ephemeris['date'][0:i],#plt_date ,
                    y = 1e3*np.array(density_model),
                      name= title_y_string, mode = 'markers',marker= dict(size =4) )

#     data = [plot_dens]

#     layout = go.Layout(
#                     xaxis=dict( title = 'Date'),
#                     yaxis=dict(type='log', autorange=True, exponentformat='power',
#                            showexponent='all',title = 'Density [km]'), 
#                     title = title_string)
    return plot_dens

# Quiet Time: 2013/03/01-2013/03/03

In [6]:
data = [
        sample_TIEGCM('../../Summer2019_data/TIEGCM_data/2013.03.01-2013.03.03_quiet/CCMC_2013.03.01.tiegcm.data/',
                              'original',
                              '2013_03_01_to_2013_03_04', 'CCMC data'),
        sample_TIEGCM('../../Summer2019_data/TIEGCM_data/2013.03.01-2013.03.03_quiet/Cheyenne_2013.03.01.tiegcm.data/',
                              'original',
                              '2013_03_01_to_2013_03_04', 'Cheyenne data'),
        sample_TIEGCM('../../Summer2019_data/TIEGCM_data/2013.03.01-2013.03.03_quiet/CCMC_2013.03.01.tiegcm.data/', 
                              'edited',
                              '2013_03_01_to_2013_03_04', 'CCMC data'),
        sample_TIEGCM('../../Summer2019_data/TIEGCM_data/2013.03.01-2013.03.03_quiet/Cheyenne_2013.03.01.tiegcm.data/', 
                              'edited',
                              '2013_03_01_to_2013_03_04', 'Cheyenne data')
       
       ]

layout = go.Layout(
                    xaxis=dict( title = 'Date'),
                    yaxis=dict(type='log', autorange=True, exponentformat='power',
                           showexponent='all',title = 'Density [km]'), 
                    title = "TIEGCM sampled using Aqua, 2013 March 01-03, Quiet time"
    )

fig = go.Figure(data=data, layout=layout)
iplot(fig)




initializing tiegcm with ../../Summer2019_data/TIEGCM_data/2013.03.01-2013.03.03_quiet/CCMC_2013.03.01.tiegcm.data/s000.nc
initializing tiegcm with ../../Summer2019_data/TIEGCM_data/2013.03.01-2013.03.03_quiet/CCMC_2013.03.01.tiegcm.data/s001.nc
initializing tiegcm with ../../Summer2019_data/TIEGCM_data/2013.03.01-2013.03.03_quiet/CCMC_2013.03.01.tiegcm.data/s002.nc
initializing tiegcm with ../../Summer2019_data/TIEGCM_data/2013.03.01-2013.03.03_quiet/CCMC_2013.03.01.tiegcm.data/s003.nc
initializing tiegcm with ../../Summer2019_data/TIEGCM_data/2013.03.01-2013.03.03_quiet/CCMC_2013.03.01.tiegcm.data/s000.nc
initializing tiegcm with ../../Summer2019_data/TIEGCM_data/2013.03.01-2013.03.03_quiet/CCMC_2013.03.01.tiegcm.data/s001.nc
initializing tiegcm with ../../Summer2019_data/TIEGCM_data/2013.03.01-2013.03.03_quiet/CCMC_2013.03.01.tiegcm.data/s002.nc
initializing tiegcm with ../../Summer2019_data/TIEGCM_data/2013.03.01-2013.03.03_quiet/CCMC_2013.03.01.tiegcm.data/s003.nc
model manager in

time =  13-03-01 22:45:00
time =  13-03-01 22:50:00
time =  13-03-01 22:55:00
time =  13-03-01 23:00:00
time =  13-03-01 23:05:00
time =  13-03-01 23:10:00
time =  13-03-01 23:15:00
time =  13-03-01 23:20:00
time =  13-03-01 23:25:00
time =  13-03-01 23:30:00
time =  13-03-01 23:35:00
time =  13-03-01 23:40:00
time =  13-03-01 23:45:00
time =  13-03-01 23:50:00
time =  13-03-01 23:55:00
time =  13-03-02 00:00:00
time =  13-03-02 00:05:00
time =  13-03-02 00:10:00
time =  13-03-02 00:15:00
time =  13-03-02 00:20:00
time =  13-03-02 00:25:00
time =  13-03-02 00:30:00
time =  13-03-02 00:35:00
time =  13-03-02 00:40:00
time =  13-03-02 00:45:00
time =  13-03-02 00:50:00
time =  13-03-02 00:55:00
time =  13-03-02 01:00:00
time =  13-03-02 01:05:00
time =  13-03-02 01:10:00
time =  13-03-02 01:15:00
time =  13-03-02 01:20:00
time =  13-03-02 01:25:00
time =  13-03-02 01:30:00
time =  13-03-02 01:35:00
time =  13-03-02 01:40:00
time =  13-03-02 01:45:00
time =  13-03-02 01:50:00
time =  13-0

time =  13-03-03 07:45:00
time =  13-03-03 07:50:00
time =  13-03-03 07:55:00
time =  13-03-03 08:00:00
time =  13-03-03 08:05:00
time =  13-03-03 08:10:00
time =  13-03-03 08:15:00
time =  13-03-03 08:20:00
time =  13-03-03 08:25:00
time =  13-03-03 08:30:00
time =  13-03-03 08:35:00
time =  13-03-03 08:40:00
time =  13-03-03 08:45:00
time =  13-03-03 08:50:00
time =  13-03-03 08:55:00
time =  13-03-03 09:00:00
time =  13-03-03 09:05:00
time =  13-03-03 09:10:00
time =  13-03-03 09:15:00
time =  13-03-03 09:20:00
time =  13-03-03 09:25:00
time =  13-03-03 09:30:00
time =  13-03-03 09:35:00
time =  13-03-03 09:40:00
time =  13-03-03 09:45:00
time =  13-03-03 09:50:00
time =  13-03-03 09:55:00
time =  13-03-03 10:00:00
time =  13-03-03 10:05:00
time =  13-03-03 10:10:00
time =  13-03-03 10:15:00
time =  13-03-03 10:20:00
time =  13-03-03 10:25:00
time =  13-03-03 10:30:00
time =  13-03-03 10:35:00
time =  13-03-03 10:40:00
time =  13-03-03 10:45:00
time =  13-03-03 10:50:00
time =  13-0

create_3Dtime_interpolator - times [0. 1.]
Slice_key4D(time=(<type 'slice'>, (0, 2, None)), height=(<type 'slice'>, (None, None, None)), latitude=(<type 'slice'>, (33, 35, None)), longitude=(<type 'slice'>, (45, 47, None)), variable='N2N')
create_3Dtime_interpolator - times [0. 1.]
Slice_key4D(time=(<type 'slice'>, (0, 2, None)), height=(<type 'slice'>, (None, None, None)), latitude=(<type 'slice'>, (32, 34, None)), longitude=(<type 'slice'>, (44, 46, None)), variable='N2N')
create_3Dtime_interpolator - times [0. 1.]
Slice_key4D(time=(<type 'slice'>, (0, 2, None)), height=(<type 'slice'>, (None, None, None)), latitude=(<type 'slice'>, (31, 33, None)), longitude=(<type 'slice'>, (43, 45, None)), variable='N2N')
time =  13-03-01 00:15:00
create_3Dtime_interpolator - times [0. 1.]
Slice_key4D(time=(<type 'slice'>, (0, 2, None)), height=(<type 'slice'>, (None, None, None)), latitude=(<type 'slice'>, (31, 33, None)), longitude=(<type 'slice'>, (43, 45, None)), variable='N2N')
create_3Dtime_

create_3Dtime_interpolator - times [0. 1.]
Slice_key4D(time=(<type 'slice'>, (0, 2, None)), height=(<type 'slice'>, (None, None, None)), latitude=(<type 'slice'>, (7, 9, None)), longitude=(<type 'slice'>, (36, 38, None)), variable='N2N')
create_3Dtime_interpolator - times [0. 1.]
Slice_key4D(time=(<type 'slice'>, (0, 2, None)), height=(<type 'slice'>, (None, None, None)), latitude=(<type 'slice'>, (6, 8, None)), longitude=(<type 'slice'>, (35, 37, None)), variable='N2N')
time =  13-03-01 00:50:00
create_3Dtime_interpolator - times [0. 1.]
Slice_key4D(time=(<type 'slice'>, (0, 2, None)), height=(<type 'slice'>, (None, None, None)), latitude=(<type 'slice'>, (6, 8, None)), longitude=(<type 'slice'>, (35, 37, None)), variable='N2N')
create_3Dtime_interpolator - times [0. 1.]
Slice_key4D(time=(<type 'slice'>, (0, 2, None)), height=(<type 'slice'>, (None, None, None)), latitude=(<type 'slice'>, (5, 7, None)), longitude=(<type 'slice'>, (34, 36, None)), variable='N2N')
create_3Dtime_interpol

...

time =  13-03-02 06:10:00
time =  13-03-02 06:15:00
time =  13-03-02 06:20:00
time =  13-03-02 06:25:00
time =  13-03-02 06:30:00
time =  13-03-02 06:35:00
time =  13-03-02 06:40:00
time =  13-03-02 06:45:00
time =  13-03-02 06:50:00
time =  13-03-02 06:55:00
time =  13-03-02 07:00:00
time =  13-03-02 07:05:00
time =  13-03-02 07:10:00
time =  13-03-02 07:15:00
time =  13-03-02 07:20:00
time =  13-03-02 07:25:00
time =  13-03-02 07:30:00
time =  13-03-02 07:35:00
time =  13-03-02 07:40:00
time =  13-03-02 07:45:00
time =  13-03-02 07:50:00
time =  13-03-02 07:55:00
time =  13-03-02 08:00:00
time =  13-03-02 08:05:00
time =  13-03-02 08:10:00
time =  13-03-02 08:15:00
time =  13-03-02 08:20:00
time =  13-03-02 08:25:00
time =  13-03-02 08:30:00
time =  13-03-02 08:35:00
time =  13-03-02 08:40:00
time =  13-03-02 08:45:00
time =  13-03-02 08:50:00
time =  13-03-02 08:55:00
time =  13-03-02 09:00:00
time =  13-03-02 09:05:00
time =  13-03-02 09:10:00
time =  13-03-02 09:15:00
40.9 -108.62

time =  13-03-03 09:10:00
time =  13-03-03 09:15:00
time =  13-03-03 09:20:00
time =  13-03-03 09:25:00
time =  13-03-03 09:30:00
time =  13-03-03 09:35:00
time =  13-03-03 09:40:00
time =  13-03-03 09:45:00
time =  13-03-03 09:50:00
time =  13-03-03 09:55:00
time =  13-03-03 10:00:00
time =  13-03-03 10:05:00
time =  13-03-03 10:10:00
time =  13-03-03 10:15:00
time =  13-03-03 10:20:00
time =  13-03-03 10:25:00
time =  13-03-03 10:30:00
time =  13-03-03 10:35:00
time =  13-03-03 10:40:00
time =  13-03-03 10:45:00
time =  13-03-03 10:50:00
time =  13-03-03 10:55:00
time =  13-03-03 11:00:00
time =  13-03-03 11:05:00
time =  13-03-03 11:10:00
time =  13-03-03 11:15:00
time =  13-03-03 11:20:00
time =  13-03-03 11:25:00
time =  13-03-03 11:30:00
time =  13-03-03 11:35:00
time =  13-03-03 11:40:00
time =  13-03-03 11:45:00
time =  13-03-03 11:50:00
time =  13-03-03 11:55:00
time =  13-03-03 12:00:00
time =  13-03-03 12:05:00
time =  13-03-03 12:10:00
time =  13-03-03 12:15:00
time =  13-0

time =  13-03-01 08:35:00
time =  13-03-01 08:40:00
time =  13-03-01 08:45:00
time =  13-03-01 08:50:00
time =  13-03-01 08:55:00
time =  13-03-01 09:00:00
time =  13-03-01 09:05:00
time =  13-03-01 09:10:00
time =  13-03-01 09:15:00
time =  13-03-01 09:20:00
time =  13-03-01 09:25:00
time =  13-03-01 09:30:00
time =  13-03-01 09:35:00
time =  13-03-01 09:40:00
time =  13-03-01 09:45:00
time =  13-03-01 09:50:00
time =  13-03-01 09:55:00
time =  13-03-01 10:00:00
time =  13-03-01 10:05:00
time =  13-03-01 10:10:00
time =  13-03-01 10:15:00
time =  13-03-01 10:20:00
time =  13-03-01 10:25:00
time =  13-03-01 10:30:00
time =  13-03-01 10:35:00
time =  13-03-01 10:40:00
time =  13-03-01 10:45:00
time =  13-03-01 10:50:00
time =  13-03-01 10:55:00
time =  13-03-01 11:00:00
time =  13-03-01 11:05:00
time =  13-03-01 11:10:00
time =  13-03-01 11:15:00
time =  13-03-01 11:20:00
time =  13-03-01 11:25:00
time =  13-03-01 11:30:00
time =  13-03-01 11:35:00
time =  13-03-01 11:40:00
time =  13-0

time =  13-03-02 10:35:00
time =  13-03-02 10:40:00
time =  13-03-02 10:45:00
time =  13-03-02 10:50:00
time =  13-03-02 10:55:00
time =  13-03-02 11:00:00
time =  13-03-02 11:05:00
time =  13-03-02 11:10:00
time =  13-03-02 11:15:00
time =  13-03-02 11:20:00
time =  13-03-02 11:25:00
time =  13-03-02 11:30:00
time =  13-03-02 11:35:00
time =  13-03-02 11:40:00
time =  13-03-02 11:45:00
time =  13-03-02 11:50:00
time =  13-03-02 11:55:00
time =  13-03-02 12:00:00
time =  13-03-02 12:05:00
time =  13-03-02 12:10:00
time =  13-03-02 12:15:00
time =  13-03-02 12:20:00
time =  13-03-02 12:25:00
time =  13-03-02 12:30:00
time =  13-03-02 12:35:00
time =  13-03-02 12:40:00
time =  13-03-02 12:45:00
time =  13-03-02 12:50:00
time =  13-03-02 12:55:00
time =  13-03-02 13:00:00
time =  13-03-02 13:05:00
time =  13-03-02 13:10:00
time =  13-03-02 13:15:00
time =  13-03-02 13:20:00
time =  13-03-02 13:25:00
time =  13-03-02 13:30:00
time =  13-03-02 13:35:00
time =  13-03-02 13:40:00
time =  13-0

time =  13-03-03 12:45:00
time =  13-03-03 12:50:00
time =  13-03-03 12:55:00
time =  13-03-03 13:00:00
time =  13-03-03 13:05:00
time =  13-03-03 13:10:00
time =  13-03-03 13:15:00
time =  13-03-03 13:20:00
time =  13-03-03 13:25:00
time =  13-03-03 13:30:00
time =  13-03-03 13:35:00
time =  13-03-03 13:40:00
time =  13-03-03 13:45:00
time =  13-03-03 13:50:00
time =  13-03-03 13:55:00
time =  13-03-03 14:00:00
time =  13-03-03 14:05:00
time =  13-03-03 14:10:00
time =  13-03-03 14:15:00
time =  13-03-03 14:20:00
time =  13-03-03 14:25:00
time =  13-03-03 14:30:00
time =  13-03-03 14:35:00
time =  13-03-03 14:40:00
time =  13-03-03 14:45:00
time =  13-03-03 14:50:00
time =  13-03-03 14:55:00
time =  13-03-03 15:00:00
time =  13-03-03 15:05:00
time =  13-03-03 15:10:00
time =  13-03-03 15:15:00
time =  13-03-03 15:20:00
time =  13-03-03 15:25:00
time =  13-03-03 15:30:00
time =  13-03-03 15:35:00
time =  13-03-03 15:40:00
time =  13-03-03 15:45:00
time =  13-03-03 15:50:00
time =  13-0

# Storm Time: 2013/03/16 - 2013/03/20

In [7]:
data = [ 
#         sample_TIEGCM_sfile('../../Summer2019_data/TIEGCM_data/2013.03.16_2013.03.20_storm/Cheyenne_2013.03.16_2013.03.20/', 'original','2013_03_16_to_2013_03_20'),
        sample_TIEGCM('../../Summer2019_data/TIEGCM_data/2013.03.16_2013.03.20_storm/Cheyenne_2013.03.16_2013.03.20/', 
                          'edited','2013_03_16_to_2013_03_20', 'Cheyenne data'),
        sample_TIEGCM('../../Summer2019_data/TIEGCM_data/2013.03.16_2013.03.20_storm/IRIDEA/main_2013_065_data-mult-fac-1p2056.0/',
                          'edited','2013_03_16_to_2013_03_20', 'IRIDEA 2.056'),
        sample_TIEGCM('../../Summer2019_data/TIEGCM_data/2013.03.16_2013.03.20_storm/IRIDEA/main_2013_065_data-mult-fac-1p0.0/', 
                          'edited','2013_03_16_to_2013_03_20', 'IRIDEA 0.0'),
       ]

layout = go.Layout(
                    xaxis=dict( title = 'Date'),
                    yaxis=dict(type='log', autorange=True, exponentformat='power',
                           showexponent='all',title = 'Density [km]'), 
                    title = "TIEGCM sampled using Aqua, 2013 March 16-20, Storm time"
    )

fig = go.Figure(data=data, layout=layout)
iplot(fig)


initializing tiegcm with ../../Summer2019_data/TIEGCM_data/2013.03.16_2013.03.20_storm/Cheyenne_2013.03.16_2013.03.20/s_075.nc
initializing tiegcm with ../../Summer2019_data/TIEGCM_data/2013.03.16_2013.03.20_storm/Cheyenne_2013.03.16_2013.03.20/s_076.nc
initializing tiegcm with ../../Summer2019_data/TIEGCM_data/2013.03.16_2013.03.20_storm/Cheyenne_2013.03.16_2013.03.20/s_077.nc
initializing tiegcm with ../../Summer2019_data/TIEGCM_data/2013.03.16_2013.03.20_storm/Cheyenne_2013.03.16_2013.03.20/s_078.nc
initializing tiegcm with ../../Summer2019_data/TIEGCM_data/2013.03.16_2013.03.20_storm/Cheyenne_2013.03.16_2013.03.20/s_079.nc
initializing tiegcm with ../../Summer2019_data/TIEGCM_data/2013.03.16_2013.03.20_storm/Cheyenne_2013.03.16_2013.03.20/s_075.nc
initializing tiegcm with ../../Summer2019_data/TIEGCM_data/2013.03.16_2013.03.20_storm/Cheyenne_2013.03.16_2013.03.20/s_076.nc
initializing tiegcm with ../../Summer2019_data/TIEGCM_data/2013.03.16_2013.03.20_storm/Cheyenne_2013.03.16_2013

time =  13-03-16 21:50:00
time =  13-03-16 21:55:00
time =  13-03-16 22:00:00
time =  13-03-16 22:05:00
time =  13-03-16 22:10:00
time =  13-03-16 22:15:00
time =  13-03-16 22:20:00
time =  13-03-16 22:25:00
time =  13-03-16 22:30:00
time =  13-03-16 22:35:00
time =  13-03-16 22:40:00
time =  13-03-16 22:45:00
time =  13-03-16 22:50:00
time =  13-03-16 22:55:00
time =  13-03-16 23:00:00
time =  13-03-16 23:05:00
time =  13-03-16 23:10:00
time =  13-03-16 23:15:00
time =  13-03-16 23:20:00
time =  13-03-16 23:25:00
time =  13-03-16 23:30:00
time =  13-03-16 23:35:00
time =  13-03-16 23:40:00
time =  13-03-16 23:45:00
time =  13-03-16 23:50:00
time =  13-03-16 23:55:00
time =  13-03-17 00:00:00
time =  13-03-17 00:05:00
time =  13-03-17 00:10:00
time =  13-03-17 00:15:00
time =  13-03-17 00:20:00
time =  13-03-17 00:25:00
time =  13-03-17 00:30:00
time =  13-03-17 00:35:00
time =  13-03-17 00:40:00
time =  13-03-17 00:45:00
time =  13-03-17 00:50:00
time =  13-03-17 00:55:00
time =  13-0

time =  13-03-18 00:00:00
time =  13-03-18 00:05:00
time =  13-03-18 00:10:00
time =  13-03-18 00:15:00
time =  13-03-18 00:20:00
time =  13-03-18 00:25:00
time =  13-03-18 00:30:00
time =  13-03-18 00:35:00
time =  13-03-18 00:40:00
time =  13-03-18 00:45:00
time =  13-03-18 00:50:00
time =  13-03-18 00:55:00
time =  13-03-18 01:00:00
time =  13-03-18 01:05:00
time =  13-03-18 01:10:00
time =  13-03-18 01:15:00
time =  13-03-18 01:20:00
time =  13-03-18 01:25:00
time =  13-03-18 01:30:00
time =  13-03-18 01:35:00
time =  13-03-18 01:40:00
time =  13-03-18 01:45:00
time =  13-03-18 01:50:00
time =  13-03-18 01:55:00
-24.02 177.91 70869000.0 2013-03-18 01:59:00 3000
time =  13-03-18 02:00:00
time =  13-03-18 02:05:00
time =  13-03-18 02:10:00
time =  13-03-18 02:15:00
time =  13-03-18 02:20:00
time =  13-03-18 02:25:00
time =  13-03-18 02:30:00
time =  13-03-18 02:35:00
time =  13-03-18 02:40:00
time =  13-03-18 02:45:00
time =  13-03-18 02:50:00
time =  13-03-18 02:55:00
time =  13-03-

time =  13-03-19 02:00:00
time =  13-03-19 02:05:00
time =  13-03-19 02:10:00
time =  13-03-19 02:15:00
time =  13-03-19 02:20:00
time =  13-03-19 02:25:00
time =  13-03-19 02:30:00
time =  13-03-19 02:35:00
time =  13-03-19 02:40:00
time =  13-03-19 02:45:00
time =  13-03-19 02:50:00
time =  13-03-19 02:55:00
time =  13-03-19 03:00:00
time =  13-03-19 03:05:00
time =  13-03-19 03:10:00
time =  13-03-19 03:15:00
time =  13-03-19 03:20:00
time =  13-03-19 03:25:00
time =  13-03-19 03:30:00
time =  13-03-19 03:35:00
time =  13-03-19 03:40:00
time =  13-03-19 03:45:00
time =  13-03-19 03:50:00
time =  13-03-19 03:55:00
time =  13-03-19 04:00:00
time =  13-03-19 04:05:00
time =  13-03-19 04:10:00
time =  13-03-19 04:15:00
time =  13-03-19 04:20:00
time =  13-03-19 04:25:00
time =  13-03-19 04:30:00
time =  13-03-19 04:35:00
time =  13-03-19 04:40:00
time =  13-03-19 04:45:00
time =  13-03-19 04:50:00
time =  13-03-19 04:55:00
time =  13-03-19 05:00:00
time =  13-03-19 05:05:00
time =  13-0

time =  13-03-20 04:05:00
time =  13-03-20 04:10:00
time =  13-03-20 04:15:00
time =  13-03-20 04:20:00
time =  13-03-20 04:25:00
time =  13-03-20 04:30:00
time =  13-03-20 04:35:00
time =  13-03-20 04:40:00
time =  13-03-20 04:45:00
time =  13-03-20 04:50:00
time =  13-03-20 04:55:00
time =  13-03-20 05:00:00
time =  13-03-20 05:05:00
time =  13-03-20 05:10:00
time =  13-03-20 05:15:00
time =  13-03-20 05:20:00
time =  13-03-20 05:25:00
time =  13-03-20 05:30:00
time =  13-03-20 05:35:00
time =  13-03-20 05:40:00
time =  13-03-20 05:45:00
time =  13-03-20 05:50:00
time =  13-03-20 05:55:00
time =  13-03-20 06:00:00
time =  13-03-20 06:05:00
time =  13-03-20 06:10:00
time =  13-03-20 06:15:00
time =  13-03-20 06:20:00
time =  13-03-20 06:25:00
time =  13-03-20 06:30:00
time =  13-03-20 06:35:00
time =  13-03-20 06:40:00
time =  13-03-20 06:45:00
time =  13-03-20 06:50:00
time =  13-03-20 06:55:00
time =  13-03-20 07:00:00
time =  13-03-20 07:05:00
time =  13-03-20 07:10:00
time =  13-0

...

time =  13-03-16 06:05:00
time =  13-03-16 06:10:00
time =  13-03-16 06:15:00
time =  13-03-16 06:20:00
time =  13-03-16 06:25:00
time =  13-03-16 06:30:00
time =  13-03-16 06:35:00
time =  13-03-16 06:40:00
time =  13-03-16 06:45:00
time =  13-03-16 06:50:00
time =  13-03-16 06:55:00
time =  13-03-16 07:00:00
time =  13-03-16 07:05:00
time =  13-03-16 07:10:00
time =  13-03-16 07:15:00
time =  13-03-16 07:20:00
time =  13-03-16 07:25:00
time =  13-03-16 07:30:00
time =  13-03-16 07:35:00
time =  13-03-16 07:40:00
time =  13-03-16 07:45:00
time =  13-03-16 07:50:00
time =  13-03-16 07:55:00
time =  13-03-16 08:00:00
time =  13-03-16 08:05:00
time =  13-03-16 08:10:00
time =  13-03-16 08:15:00
time =  13-03-16 08:20:00
time =  13-03-16 08:25:00
time =  13-03-16 08:30:00
time =  13-03-16 08:35:00
time =  13-03-16 08:40:00
time =  13-03-16 08:45:00
time =  13-03-16 08:50:00
time =  13-03-16 08:55:00
time =  13-03-16 09:00:00
time =  13-03-16 09:05:00
time =  13-03-16 09:10:00
time =  13-0

time =  13-03-17 08:15:00
time =  13-03-17 08:20:00
time =  13-03-17 08:25:00
time =  13-03-17 08:30:00
time =  13-03-17 08:35:00
time =  13-03-17 08:40:00
time =  13-03-17 08:45:00
time =  13-03-17 08:50:00
time =  13-03-17 08:55:00
time =  13-03-17 09:00:00
time =  13-03-17 09:05:00
time =  13-03-17 09:10:00
time =  13-03-17 09:15:00
-63.58 81.15 71071000.0 2013-03-17 09:19:00 2000
time =  13-03-17 09:20:00
time =  13-03-17 09:25:00
time =  13-03-17 09:30:00
time =  13-03-17 09:35:00
time =  13-03-17 09:40:00
time =  13-03-17 09:45:00
time =  13-03-17 09:50:00
time =  13-03-17 09:55:00
time =  13-03-17 10:00:00
time =  13-03-17 10:05:00
time =  13-03-17 10:10:00
time =  13-03-17 10:15:00
time =  13-03-17 10:20:00
time =  13-03-17 10:25:00
time =  13-03-17 10:30:00
time =  13-03-17 10:35:00
time =  13-03-17 10:40:00
time =  13-03-17 10:45:00
time =  13-03-17 10:50:00
time =  13-03-17 10:55:00
time =  13-03-17 11:00:00
time =  13-03-17 11:05:00
time =  13-03-17 11:10:00
time =  13-03-1

time =  13-03-18 10:15:00
time =  13-03-18 10:20:00
time =  13-03-18 10:25:00
time =  13-03-18 10:30:00
time =  13-03-18 10:35:00
time =  13-03-18 10:40:00
time =  13-03-18 10:45:00
time =  13-03-18 10:50:00
time =  13-03-18 10:55:00
time =  13-03-18 11:00:00
time =  13-03-18 11:05:00
time =  13-03-18 11:10:00
time =  13-03-18 11:15:00
time =  13-03-18 11:20:00
time =  13-03-18 11:25:00
time =  13-03-18 11:30:00
time =  13-03-18 11:35:00
time =  13-03-18 11:40:00
time =  13-03-18 11:45:00
time =  13-03-18 11:50:00
time =  13-03-18 11:55:00
time =  13-03-18 12:00:00
time =  13-03-18 12:05:00
time =  13-03-18 12:10:00
time =  13-03-18 12:15:00
time =  13-03-18 12:20:00
time =  13-03-18 12:25:00
time =  13-03-18 12:30:00
time =  13-03-18 12:35:00
time =  13-03-18 12:40:00
time =  13-03-18 12:45:00
time =  13-03-18 12:50:00
time =  13-03-18 12:55:00
time =  13-03-18 13:00:00
time =  13-03-18 13:05:00
time =  13-03-18 13:10:00
time =  13-03-18 13:15:00
time =  13-03-18 13:20:00
time =  13-0

time =  13-03-19 12:15:00
time =  13-03-19 12:20:00
time =  13-03-19 12:25:00
time =  13-03-19 12:30:00
time =  13-03-19 12:35:00
time =  13-03-19 12:40:00
time =  13-03-19 12:45:00
time =  13-03-19 12:50:00
time =  13-03-19 12:55:00
time =  13-03-19 13:00:00
time =  13-03-19 13:05:00
time =  13-03-19 13:10:00
time =  13-03-19 13:15:00
time =  13-03-19 13:20:00
time =  13-03-19 13:25:00
time =  13-03-19 13:30:00
time =  13-03-19 13:35:00
time =  13-03-19 13:40:00
time =  13-03-19 13:45:00
time =  13-03-19 13:50:00
time =  13-03-19 13:55:00
time =  13-03-19 14:00:00
time =  13-03-19 14:05:00
time =  13-03-19 14:10:00
time =  13-03-19 14:15:00
time =  13-03-19 14:20:00
time =  13-03-19 14:25:00
time =  13-03-19 14:30:00
time =  13-03-19 14:35:00
time =  13-03-19 14:40:00
time =  13-03-19 14:45:00
time =  13-03-19 14:50:00
time =  13-03-19 14:55:00
time =  13-03-19 15:00:00
time =  13-03-19 15:05:00
time =  13-03-19 15:10:00
time =  13-03-19 15:15:00
time =  13-03-19 15:20:00
time =  13-0

time =  13-03-20 14:25:00
time =  13-03-20 14:30:00
time =  13-03-20 14:35:00
time =  13-03-20 14:40:00
time =  13-03-20 14:45:00
time =  13-03-20 14:50:00
time =  13-03-20 14:55:00
time =  13-03-20 15:00:00
time =  13-03-20 15:05:00
time =  13-03-20 15:10:00
time =  13-03-20 15:15:00
time =  13-03-20 15:20:00
time =  13-03-20 15:25:00
time =  13-03-20 15:30:00
time =  13-03-20 15:35:00
time =  13-03-20 15:40:00
time =  13-03-20 15:45:00
time =  13-03-20 15:50:00
time =  13-03-20 15:55:00
time =  13-03-20 16:00:00
time =  13-03-20 16:05:00
time =  13-03-20 16:10:00
time =  13-03-20 16:15:00
time =  13-03-20 16:20:00
time =  13-03-20 16:25:00
time =  13-03-20 16:30:00
time =  13-03-20 16:35:00
time =  13-03-20 16:40:00
time =  13-03-20 16:45:00
time =  13-03-20 16:50:00
time =  13-03-20 16:55:00
time =  13-03-20 17:00:00
time =  13-03-20 17:05:00
time =  13-03-20 17:10:00
time =  13-03-20 17:15:00
time =  13-03-20 17:20:00
time =  13-03-20 17:25:00
time =  13-03-20 17:30:00
time =  13-0

In [8]:



# def sample_TIEGCM_iregular(files, tiegcm_version, time_string):
#     if tiegcm_version == "original":
#         tiegcm = Model_Manager_o(files)
#     elif tiegcm_version == "edited":
# #         tiegcm = Model_Manager(files)
#         tiegcm = TIEGCM(files)
    
#     for iday in tiegcm.rootgrp['day']: #want from day 75 through 79
# days_want = [75,76,77,78,79]
# print days_want
# #         if iday in days_want:
        
            
            
            
            
#     aqua_ephemeris = import_ephemeris(time_string)
#     date_formatted = aqua_ephemeris['date'].dt.strftime('%y-%m-%d %H:%M:%S')
#     for i,idate in enumerate(aqua_ephemeris['date']):
#         xlon = np.round(np.array(aqua_ephemeris['lon'][i]) , decimals=2)
#         xlat = np.round(np.array(aqua_ephemeris['lat'][i])  , decimals=2)
#         xalt = np.round(aqua_ephemeris['altitude'][i] , decimals=2) *1e5
#         idate = aqua_ephemeris['date'][i]
#         time = date_formatted[i]
#         print 'time = ', time
#         density_model.append(tiegcm.density(xlat, xlon, xalt,  idate ))

        
#     plot_dens = go.Scatter(
#                     x = aqua_ephemeris['date'][0:i],#plt_date ,
#                     y = 1e3*np.array(density_model),
#                       name= title_y_string, mode = 'markers',marker= dict(size =4) )

#     data = [plot_dens]

#     layout = go.Layout(
#                     xaxis=dict( title = 'Date'),
#                     yaxis=dict(type='log', autorange=True, exponentformat='power',
#                            showexponent='all',title = 'Density [km]'), 
#                     title = title_string)
#     return #plot_dens

In [9]:
# files = '../data/TIEGCM_data/2013.03.16_2013.03.20_storm/IRIDEA/main_2013_065_data-mult-fac-1p2056.0/it_3_dir/sechist_iter3.nc'

# sample_TIEGCM_iregular(files, 'edited','2013_03_01_to_2013_03_04')


In [10]:
# tiegcm = TIEGCM('../data/TIEGCM_data/2013.03.16_2013.03.20_storm/IRIDEA/main_2013_065_data-mult-fac-1p2056.0/it_3_dir/sechist_iter3.nc')
# model = Model_Manager(directory='../data/TIEGCM_data/2013.03.16_2013.03.20_storm/IRIDEA/main_2013_065_data-mult-fac-1p2056.0/it_3_dir/',)
